# Definitions 

amount_tsh - Total static head (amount water available to waterpoint)

date_recorded - The date the row was entered

funder - Who funded the well

gps_height - Altitude of the well

installer - Organization that installed the well

longitude - GPS coordinate 

latitude - GPS coordinate

wpt_name - Name of the waterpoint if there is one

num_private - 

basin - Geographic water basin

subvillage - Geographic location

region - Geographic location

region_code - Geographic location (coded)

district_code - Geographic location (coded)

lga - Geographic location

ward - Geographic location

population - Population around the well

public_meeting - True/False

recorded_by - Group entering this row of data

scheme_management - Who operates the waterpoint

scheme_name - Who operates the waterpoint

permit - If the waterpoint is permitted

construction_year - Year the waterpoint was constructed

extraction_type - The kind of extraction the waterpoint uses

extraction_type_group - The kind of extraction the waterpoint uses

extraction_type_class - The kind of extraction the waterpoint uses

management - How the waterpoint is managed

management_group - How the waterpoint is managed

payment - What the water costs

payment_type - What the water costs

water_quality - The quality of the water

quality_group - The quality of the water

quantity - The quantity of water

quantity_group - The quantity of water

source - The source of the water

source_type - The source of the water

source_class - The source of the water

waterpoint_type - The kind of waterpoint

waterpoint_type_group - The kind of waterpoint

# Package Installation

In [2]:
import pandas as pd
import pandas as np
import geopandas as geo
import warnings
warnings.filterwarnings('ignore')
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier 
from sklearn.preprocessing import OneHotEncoder
from sklearn.tree import DecisionTreeClassifier 
from sklearn.metrics import accuracy_score
from sklearn.tree import export_graphviz
from IPython.display import Image  
from pydotplus import graph_from_dot_data
from IPython.display import display
from sklearn.model_selection import GridSearchCV


The labels in this dataset are simple. There are three possible values:
functional - the waterpoint is operational and there are no repairs needed
functional needs repair - the waterpoint is operational, but needs repairs
non functional - the waterpoint is not operational

# Dataset

In [3]:
X = pd.read_csv('Data/X.csv')
y = pd.read_csv('Data/Y.csv')
X1 = pd.read_csv('Data/X1.csv')

df = pd.merge(y,X,on='id')

In [4]:
df.head()

id    status_group  amount_tsh date_recorded        funder  gps_height  \
0  69572      functional      6000.0    2011-03-14         Roman        1390   
1   8776      functional         0.0    2013-03-06       Grumeti        1399   
2  34310      functional        25.0    2013-02-25  Lottery Club         686   
3  67743  non functional         0.0    2013-01-28        Unicef         263   
4  19728      functional         0.0    2011-07-13   Action In A           0   

      installer  longitude   latitude              wpt_name  ...  \
0         Roman  34.938093  -9.856322                  none  ...   
1       GRUMETI  34.698766  -2.147466              Zahanati  ...   
2  World vision  37.460664  -3.821329           Kwa Mahundi  ...   
3        UNICEF  38.486161 -11.155298  Zahanati Ya Nanyumbu  ...   
4       Artisan  31.130847  -1.825359               Shuleni  ...   

   payment_type water_quality quality_group      quantity  quantity_group  \
0      annually          soft          good        enough          enough   
1     never pay          soft          good  insufficient    insufficient   
2    per bucket          soft          good        enough          enough   
3     never pay          soft          good           dry             dry   
4     never pay          soft          good      seasonal        seasonal   

                 source           source_type source_class  \
0                spring                spring  groundwater   
1  rainwater harvesting  rainwater harvesting      surface   
2                   dam                   dam      surface   
3           machine dbh              borehole  groundwater   
4  rainwater harvesting  rainwater harvesting      surface   

               waterpoint_type waterpoint_type_group  
0           communal standpipe    communal standpipe  
1           communal standpipe    communal standpipe  
2  communal standpipe multiple    communal standpipe  
3  communal standpipe multiple    communal standpipe  
4           communal standpipe    communal standpipe  

[5 rows x 41 columns]

In [5]:
non_func = df[df['status_group'] == 'non functional']
non_func['funder'].value_counts()

Government Of Tanzania    4663
Danida                    1242
Hesawa                    1034
World Bank                 707
Kkkt                       498
                          ... 
Busoga Trust                 1
Cvs Miss                     1
Imf                          1
Selikali Ya Kijiji           1
Ripati                       1
Name: funder, Length: 1019, dtype: int64

In [6]:
df['funder'].value_counts()

Government Of Tanzania    9084
Danida                    3114
Hesawa                    2202
Rwssp                     1374
World Bank                1349
                          ... 
Rc Missi                     1
Asgerali N Bharwan           1
Aqua Blues Angels            1
Balyehe                      1
Mtambo                       1
Name: funder, Length: 1897, dtype: int64

In [7]:
df.isnull().sum()

id                           0
status_group                 0
amount_tsh                   0
date_recorded                0
funder                    3635
gps_height                   0
installer                 3655
longitude                    0
latitude                     0
wpt_name                     0
num_private                  0
basin                        0
subvillage                 371
region                       0
region_code                  0
district_code                0
lga                          0
ward                         0
population                   0
public_meeting            3334
recorded_by                  0
scheme_management         3877
scheme_name              28166
permit                    3056
construction_year            0
extraction_type              0
extraction_type_group        0
extraction_type_class        0
management                   0
management_group             0
payment                      0
payment_type                 0
water_qu

In [8]:
df['installer'].fillna('other', inplace = True)
df['funder'].fillna('other', inplace = True)
df['public_meeting'].fillna('False', inplace = True)
df['scheme_management'].fillna('other',inplace = True)
df['permit'].fillna('False', inplace = True)
df['scheme_name'].fillna('other', inplace = True)
df.dropna(subset=['subvillage'],inplace = True)
df.drop(columns =['recorded_by','construction_year'], inplace = True)

In [9]:
df.isnull().sum()

id                       0
status_group             0
amount_tsh               0
date_recorded            0
funder                   0
gps_height               0
installer                0
longitude                0
latitude                 0
wpt_name                 0
num_private              0
basin                    0
subvillage               0
region                   0
region_code              0
district_code            0
lga                      0
ward                     0
population               0
public_meeting           0
scheme_management        0
scheme_name              0
permit                   0
extraction_type          0
extraction_type_group    0
extraction_type_class    0
management               0
management_group         0
payment                  0
payment_type             0
water_quality            0
quality_group            0
quantity                 0
quantity_group           0
source                   0
source_type              0
source_class             0
w

In [10]:
df.sample(n=20)

id             status_group  amount_tsh date_recorded  \
15916  42792               functional         0.0    2013-03-13   
46783  65212               functional        20.0    2011-03-07   
10278  43637               functional       300.0    2011-03-21   
58344  42346           non functional         0.0    2013-02-27   
55266   3011               functional       600.0    2013-01-27   
34232   8196           non functional         0.0    2011-07-28   
6909   71410               functional         0.0    2011-07-16   
54196  26458           non functional         0.0    2011-07-19   
11390   7069           non functional         0.0    2011-03-15   
41504  62785               functional        20.0    2011-02-28   
47066  58452           non functional         0.0    2011-07-26   
30596  61835               functional         0.0    2012-10-16   
31011  35215               functional         0.0    2011-07-30   
1296   71021               functional      1200.0    2011-03-26   
25690   4540  functional needs repair         0.0    2011-08-18   
48262  61480               functional         0.0    2013-03-16   
27966  33358           non functional         0.0    2012-11-13   
2135   51984               functional         0.0    2011-08-02   
5645   65692               functional        30.0    2011-04-10   
24913   2031               functional         0.0    2013-02-16   

                  funder  gps_height           installer  longitude  \
15916              Tasaf        1445                 DWE  36.748762   
46783                Wua         312                  WU  38.298762   
10278                 Co         298                  Co  36.997969   
58344             Danida        1499              DANIDA  34.929413   
55266                Isf         813                 DWE  29.736149   
34232             Danida           0  Central government  33.895141   
6909               Kaemp           0      LOCAL CONTRACT  31.580575   
54196             Danida           0  Central government  33.879302   
11390              Unice         188                 RWE  37.852071   
41504      Water User As         243                  Wa  38.353637   
47066                 Si           0                  SI  31.583642   
30596        Netherlands           0                 DWE  34.002866   
31011             Unicef           0                 DWE  33.087149   
1296               Conce        1391                 DWE  34.766642   
25690               Kkkt           0                KKKT  32.829584   
48262              other         941               other  35.852442   
27966  Ministry Of Water        1151              Hesawa  33.945866   
2135                 Wvt           0                 WVT  34.418848   
5645                  Dh           0                  DH  37.342838   
24913               Undp         463          Government  34.936838   

        latitude               wpt_name  ...  payment_type water_quality  \
15916  -3.359655                Ofisini  ...     never pay          soft   
46783  -6.122426                  Daudi  ...    per bucket          soft   
10278  -7.597820              Kwa Shani  ...    on failure      coloured   
58344 -10.971496        Kwa Mzee Jabali  ...     never pay          soft   
55266  -4.850132            Kwa Damiano  ...       monthly          soft   
34232  -9.455654    Kwa Nyasa Andongile  ...       monthly          soft   
6909   -1.410951     Kwa John Karungura  ...      annually          soft   
54196  -9.585923  Kwa Atupele Mwaisimba  ...     never pay          soft   
11390  -7.124704         Kwa Mzee Ngoma  ...     never pay         salty   
41504  -6.378016                  Fungo  ...    per bucket          soft   
47066  -1.787840            Kwa Ponsian  ...     never pay          soft   
30596  -3.231008               Victoria  ...         other          soft   
31011  -2.414892     Shuleni Lutale Sec  ...     never pay          soft   
1296   -8.572263                   none  ...  

In [11]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 59029 entries, 0 to 59399
Data columns (total 39 columns):
id                       59029 non-null int64
status_group             59029 non-null object
amount_tsh               59029 non-null float64
date_recorded            59029 non-null object
funder                   59029 non-null object
gps_height               59029 non-null int64
installer                59029 non-null object
longitude                59029 non-null float64
latitude                 59029 non-null float64
wpt_name                 59029 non-null object
num_private              59029 non-null int64
basin                    59029 non-null object
subvillage               59029 non-null object
region                   59029 non-null object
region_code              59029 non-null int64
district_code            59029 non-null int64
lga                      59029 non-null object
ward                     59029 non-null object
population               59029 non-null int64
p

# Initial split of DataSet (Train / Test set)

In [19]:
y = df['status_group']
X = df.loc[:, ['installer', 'payment_type', 'water_quality', 'source_class', 'waterpoint_type']] # Confirm the number of independent variables
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42, train_size=0.67)


# Baseline Model - Decision Tree

In [17]:
X_ohe = pd.get_dummies(X_train, prefix = ['installer','payment_type', 'water_quality',  'source_class','waterpoint_type'])
y_ohe = pd.get_dummies(y_train, prefix = ['status_group'])

In [14]:
clf = DecisionTreeClassifier(criterion='entropy', max_depth = 100, min_samples_leaf = 500)
clf.fit(X_ohe, y_ohe)

DecisionTreeClassifier(class_weight=None, criterion='entropy', max_depth=100,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=500, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [15]:
y_preds = clf.predict(X_ohe)
print('Accuracy: ', accuracy_score(y_ohe, y_preds))

Accuracy:  0.5907102581607626


In [18]:
clf = DecisionTreeClassifier(criterion='entropy', max_depth = 5, min_samples_leaf = 200)
clf.fit(X_ohe, y_ohe) #encoded categorical variable using pd.get_dummies()

from sklearn.tree import export_graphviz
# Export as dot file
export_graphviz(clf, out_file='tree.dot', 
                feature_names = X_ohe.columns,
                class_names = np.unique(y).astype(str),
                rounded = True, proportion = False, 
                precision = 2, filled = True)

# Convert to png 
from subprocess import call
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree.png')

In [ ]:
clf1 = DecisionTreeClassifier()
param_grid = {'criterion':['gini','entropy'], 'max_depth': [5,10,15,20,50], 'min_samples_leaf':[100, 200, 300, 400]}
gs = GridSearchCV(clf1, param_grid, cv = 5)

gs.fit(X_ohe, y_ohe)
gs.best_params_